In [1]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
Created on Wed Jun  3 12:57:49 2020

@author: josephharvey
"""
from datetime import datetime
from lorenzrungekutta_numba import rungekutta
# from lorenzrungekutta_numba import fx
# from lorenzrungekutta_numba import fy
# from lorenzrungekutta_numba import fz
import numpy as np
#from sklearn.linear_model import Ridge
from scipy import sparse
from scipy.linalg import solve
from scipy.optimize import minimize
from scipy.sparse.linalg import eigs
from scipy.stats import wasserstein_distance
from matplotlib import pyplot as plt

class Reservoir:
    def __init__(self, rk, rsvr_size = 300, spectral_radius = 0.6, input_weight = 1):
        self.rsvr_size = rsvr_size
        
        #get spectral radius < 1
        #gets row density = 0.03333
        unnormalized_W = (np.random.rand(rsvr_size,rsvr_size)*2 - 1)
        for i in range(unnormalized_W[:,0].size):
            for j in range(unnormalized_W[0].size):
                if np.random.rand(1) > 10/rsvr_size:
                    unnormalized_W[i][j] = 0
    
        max_eig = eigs(unnormalized_W, k = 1, return_eigenvectors = False, maxiter = 10**5)
        
        self.W = sparse.csr_matrix(spectral_radius/np.abs(max_eig)*unnormalized_W)
        
        const_conn = int(rsvr_size*0.15)
        Win = np.zeros((rsvr_size, 4))
        Win[:const_conn, 0] = (np.random.rand(Win[:const_conn, 0].size)*2 - 1)*input_weight
        Win[const_conn: const_conn + int((rsvr_size-const_conn)/3), 1] = (np.random.rand(Win[const_conn: const_conn + int((rsvr_size-const_conn)/3), 1].size)*2 - 1)*input_weight
        Win[const_conn + int((rsvr_size-const_conn)/3):const_conn + 2*int((rsvr_size-const_conn)/3), 2] = (np.random.rand(Win[const_conn + int((rsvr_size-const_conn)/3):const_conn + 2*int((rsvr_size-const_conn)/3), 2].size)*2 - 1)*input_weight
        Win[const_conn + 2*int((rsvr_size-const_conn)/3):, 3] = (np.random.rand(Win[const_conn + 2*int((rsvr_size-const_conn)/3):, 3].size)*2 - 1)*input_weight
        
        self.Win = sparse.csr_matrix(Win)
        self.X = (np.random.rand(rsvr_size, rk.train_length+2)*2 - 1)
        self.Wout = np.array([])

        self.data_trstates = 0
        self.states_trstates = 0
        
class RungeKutta:
    def __init__(self, x0 = 2,y0 = 2,z0 = 23, h = 0.01, T = 300, ttsplit = 5000, noise_scaling = 0):
        u_arr = rungekutta(x0,y0,z0,h,T)[:, ::10] 
        self.train_length = ttsplit
        
        u_arr[0] = (u_arr[0] - 0)/7.929788629895004
        u_arr[1] = (u_arr[1] - 0)/8.9932616136662
        u_arr[2] = (u_arr[2] - 23.596294463016896)/8.575917849311919
        
        self.u_arr_train = u_arr[:, :ttsplit+1] 
        #size 5001
        
        #noisy training array
        #switch to gaussian 
        noise = np.random.randn(self.u_arr_train[:,0].size, self.u_arr_train[0,:].size)*noise_scaling 
        self.u_arr_train_noise = self.u_arr_train + noise
        
        #plt.plot(self.u_arr_train_noise[0, :500])
        
        #u[5000], the 5001st element, is the last in u_arr_train and the first in u_arr_test
        self.u_arr_test = u_arr[:, ttsplit:]
        #size 1001
    
#takes a reservoir object res along with initial conditions
def getX(res, rk,x0 = 1,y0 = 1,z0 = 1, noise = False):
    
    if noise:
        u_training = rk.u_arr_train_noise
    else:
        u_training = rk.u_arr_train
    
    #loops through every timestep
    for i in range(0, u_training[0].size):
        u = np.append(1, u_training[:,i]).reshape(4,1)
        
        x = res.X[:,i].reshape(res.rsvr_size,1)
        x_update = np.tanh(np.add(res.Win.dot(u), res.W.dot(x)))
        
        res.X[:,i+1] = x_update.reshape(1,res.rsvr_size)    
    
    return res.X

def get_states(res, rk, skip = 150):
    Y_train = rk.u_arr_train_noise[:, skip+1:]
    X = getX(res, rk, noise = True)[:, skip+1:(res.X[0].size - 1)]
    X_train = np.concatenate((np.ones((1, rk.u_arr_train[0].size-(skip+1))), X, rk.u_arr_train_noise[:, skip:-1]), axis = 0)
    res.data_trstates = np.matmul(Y_train, np.transpose(X_train))
    res.states_trstates = np.matmul(X_train,np.transpose(X_train))

    return 
    
def trainRRM(res, rk, skip = 150, alpha = 10**-4):
    print("Training... ")

    alph = alpha
    #rrm = Ridge(alpha = alph, solver = 'cholesky')
    
    Y_train = rk.u_arr_train_noise[:, skip+1:]

    
    X = getX(res, rk, noise = True)[:, skip+1:(res.X[0].size - 1)]
    X_train = np.concatenate((np.ones((1, rk.u_arr_train[0].size-(skip+1))), X, rk.u_arr_train_noise[:, skip:-1]), axis = 0) 
    #X_train = np.copy(X)
    
    idenmat = np.identity(res.rsvr_size+4)*alph
    data_trstates = np.matmul(Y_train, np.transpose(X_train))
    states_trstates = np.matmul(X_train,np.transpose(X_train))
    res.Wout = np.transpose(solve(np.transpose(states_trstates + idenmat),np.transpose(data_trstates)))
    
    #optimization function needs perc. of stable res. 
    #scipy.optimize.minimize
    #https://docs.scipy.org/doc/scipy/reference/generated/scipy.optimize.minimize.html#scipy.optimize.minimize
    
    #function which takes log of alpha, give perc. of stable reservoirs

    #split up train function to find matrices first, second one which computed Wout
    #https://docs.scipy.org/doc/scipy/reference/generated/scipy.optimize.fminbound.html 
    #allows to set range of alpha

    print("Training complete ")
    #Y_train = Y_train.transpose()
    #X_train = X.transpose()
    
    #tweak regression param? use 10^-4, 10^-6
    #test Ridge() in simpler context
    #rrm.fit(X_train,Y_train)
    #res.Wout = rrm.coef_
    return res.Wout

def repeatTraining(res, T = 300, ttsplit = int(300/0.1), repeat_times = 10, skip = 150, noise_scaling = 0.1):
    ic = np.random.rand(3)*2-1
    rk = RungeKutta(x0 = ic[0], y0 = ic[1], z0 = 30*ic[2], T = T, ttsplit = ttsplit, noise_scaling = noise_scaling)
    
    print("Training... ")

    alph = 10**-6
    #rrm = Ridge(alpha = alph, solver = 'cholesky')
    
    #train on 10 small training sets with different noise - minimize error over all
    #save the state of the reservoir for noisy datasets
    #also try - train on signal^2 or other function (get more info than just 3 vars) - no noise
    
    Y_train = rk.u_arr_train[:, skip+1:] 
    oneTime = rk.u_arr_train[:, skip+1:]
    
    X = getX(res, rk, noise = True)[:, skip+1:-1]
    
    Y_inputs = rk.u_arr_train_noise[:, skip:(rk.u_arr_train_noise[0].size - 1)]
    for i in range(repeat_times-1):
        Y_train = np.concatenate((Y_train, oneTime), axis = 1)
        noise = np.random.randn(rk.u_arr_train[:,0].size, rk.u_arr_train[0,:].size)*noise_scaling
        rk.u_arr_train_noise = rk.u_arr_train + noise 
        X = np.concatenate((X, getX(res, rk, noise = True)[:, skip+1:-1]), axis = 1)
        Y_inputs = np.concatenate((Y_inputs, rk.u_arr_train_noise[:, skip:(rk.u_arr_train_noise[0].size - 1)]), axis = 1) 
        
    X_train = np.concatenate((np.ones((1, repeat_times*(rk.u_arr_train[0].size-(skip+1)))), X, Y_inputs), axis = 0) 
    #X_train = np.copy(X)
    
    idenmat = np.identity(res.rsvr_size+4)*alph
    data_trstates = np.matmul(Y_train, np.transpose(X_train))
    states_trstates = np.matmul(X_train,np.transpose(X_train))
    res.Wout = np.transpose(solve(np.transpose(states_trstates + idenmat),np.transpose(data_trstates)))
    
    print("Training complete ")
    #Y_train = Y_train.transpose()
    #X_train = X.transpose()
    
    #tweak regression param? use 10^-4, 10^-6
    #test Ridge() in simpler context
    #rrm.fit(X_train,Y_train)
    #res.Wout = rrm.coef_
    return res.Wout 

def repeatTrainingAvg(res, T = 100, ttsplit = 400, repeat_times = 10, noise_scaling = 0.01): 
    rk = RungeKutta(T = T,ttsplit = ttsplit) 
    Wout_final = np.zeros((3,res.rsvr_size+4))
    
    for i in range(repeat_times):
        noise = np.random.randn(rk.u_arr_train[:,0].size, rk.u_arr_train[0,:].size)*noise_scaling 
        rk.u_arr_train_noise = rk.u_arr_train + noise
        Wout_final = np.add(Wout_final, trainRRM(res, rk, skip = 100))
    
    res.Wout = Wout_final/repeat_times
    
#CONCATENATE ALL THE DATA BEFORE RUNNING REGRESSION
    
def predict(res, x0 = 0, y0 = 0, z0 = 0, steps = 1000):
    Y = np.empty((3, steps + 1))
    X = np.empty((res.rsvr_size, steps + 1))
    
    Y[:,0] = np.array([x0,y0,z0]).reshape(1,3) 
    X[:,0] = res.X[:,-2]

    
    for i in range(0, steps):
        y_in = np.append(1, Y[:,i]).reshape(4,1)
        x_prev = X[:,i].reshape(res.rsvr_size,1)
        
        x_current = np.tanh(np.add(res.Win.dot(y_in), res.W.dot(x_prev)))
        X[:,i+1] = x_current.reshape(1,res.rsvr_size)
        #X = np.concatenate((X, x_current), axis = 1)
        y_out = np.matmul(res.Wout, np.concatenate((np.array([[1]]), x_current, Y[:,i].reshape(3,1)), axis = 0))
        #y_out = np.matmul(res.Wout, x_current)
        Y[:,i+1] = y_out.reshape(1, 3)
        

    return Y

def test(res, num_tests = 10, rkTime = 1000, split = 3000, showMapError = True, showTrajectories = True, showHist = True):

    stable_count = 0
    valid_time = np.array([])
    max_sum_square = np.array([])
    mean_sum_square = np.array([]) 
    means = np.zeros(num_tests)
    variances = np.zeros(num_tests)
    
    for i in range(num_tests):
        
        vtchange = 0
        x2y2z2 = np.array([])
    
        ic = np.random.rand(3)*2-1
        rktest = RungeKutta(x0 = ic[0], y0 = ic[1], z0 = 30*ic[2], T = rkTime, ttsplit = split)
        res.X = (np.zeros((res.rsvr_size, split+2))*2 - 1)
        
        #sets res.X
        getX(res, rktest)
        
        pred = predict(res, x0 = rktest.u_arr_test[0,0], y0 = rktest.u_arr_test[1,0], z0 = rktest.u_arr_test[2,0], steps = (int(rkTime/0.1)-split))
        lorenz_map_x = np.zeros(pred[0].size)
        lorenz_map_x[0] = pred[0][0]
        
        check_vt = True
        for j in range(0, pred[0].size):
            if (j > 0):
                vtchange = vtchange + (rktest.u_arr_test[0, j] - rktest.u_arr_test[0, j-1])**2 + (rktest.u_arr_test[1, j] - rktest.u_arr_test[1, j-1])**2 + (rktest.u_arr_test[2, j] - rktest.u_arr_test[2, j-1])**2
                
                rkmap = RungeKutta(pred[0][j-1]*7.929788629895004, pred[1][j-1]*8.9932616136662, pred[2][j-1]*8.575917849311919+23.596294463016896, h=0.01, T=0.1)
                lorenz_map_x[j] = rkmap.u_arr_train[0][1] 
                
                #EXAMINE!!!
                x2error = (pred[0][j]-rkmap.u_arr_train[0][1])**2
                y2error = (pred[1][j]-rkmap.u_arr_train[1][1])**2
                z2error = (pred[2][j]-rkmap.u_arr_train[2][1])**2
                
                x2y2z2 = np.append(x2y2z2, (x2error+y2error+z2error)) 
                
            if (np.abs(pred[0, j] - rktest.u_arr_test[0, j]) > 1.5) and check_vt:
                valid_time = np.append(valid_time, j)
                
                print("Test " + str(i) + " valid time: " + str(j))
                check_vt = False
        
        x2y2z2 = x2y2z2/1.45
        #print(vtchange/(pred[0].size-1)) 
        #print("Mean: " + str(np.mean(pred[0])))
        #print("Variance: " + str(np.var(pred[0])))
        
        if showHist:
            plt.figure() 
            plt.hist(pred[0], bins = 11, label = "Predictions", alpha = 0.75)
            plt.hist(rktest.u_arr_test[0], bins = 11, label = "Truth", alpha = 0.75)
            plt.legend(loc="upper right")
        
        if showMapError:
            #plt.figure()
            #plt.plot(vector_field, label = "Vector Field Stability Metric")
            #plt.legend(loc="upper right") 

            plt.figure() 
            plt.plot(x2y2z2, label = "x + y + z square error")
            plt.legend(loc="upper right")
            
        if showTrajectories:
            plt.figure() 
            #plt.plot(lorenz_map_x, label = "Map Trajectory", color = "green") 
            plt.plot(pred[0], label = "Predictions")
            plt.plot(rktest.u_arr_test[0], label = "Truth") 
            plt.legend(loc="upper right") 
        
        print("Variance of lorenz data x dim: " + str(np.var(rktest.u_arr_test[0])))
        print("Variance of predictions: " + str(np.var(pred[0]))) 
        print("Max of total square error: " + str(max(x2y2z2)))
        print("Mean of total error: " + str(np.mean(x2y2z2)))
        print("Wasserstein distance: " + str(wasserstein_distance(pred[0], rktest.u_arr_test[0])))
        print()
        
        max_sum_square = np.append(max_sum_square, max(x2y2z2))
        mean_sum_square = np.append(mean_sum_square, np.mean(x2y2z2)) 
        
        means[i] = np.mean(pred[0])
        variances[i] = np.var(pred[0])
        
        if np.mean(x2y2z2) < 0.01 and 0.98 < np.var(pred[0]) and np.var(pred[0]) < 1.01:
            stable_count += 1
            print("stable")
            print()
        else:
            print("unstable")
            print() 
        
    
    
    if showMapError or showTrajectories or showHist:
        plt.show()
    
    #print("Variance of total square error: " + str(np.var(x2y2z2)))

    print("Avg. max sum square: " + str(np.mean(max_sum_square)))
    print("Avg. mean sum square: " + str(np.mean(mean_sum_square))) 
    print("Avg. of x dim: " + str(np.mean(means)))
    print("Var. of x dim: " + str(np.mean(variances)))
    print()
    
    
    return stable_count/num_tests

def generate_res(num_res, rk, res_size):

    reservoirs = []

    while len(reservoirs) < num_res:
        try:
            reservoirs.append(Reservoir(rk, rsvr_size = res_size, spectral_radius = 0.5, input_weight = 1.0))
            get_states(reservoirs[-1], rk, skip = 150) 
        except:
            print("eigenvalue error occured.")
    return reservoirs

def optim_func(reservoirs, alpha):

    results = np.array([])

    for res in reservoirs: 
        try:
            idenmat = np.identity(res.rsvr_size+4)*alpha
            res.Wout = np.transpose(solve(np.transpose(res.states_trstates + idenmat),np.transpose(res.data_trstates))) 

            results = np.append(results, test(res, 1, rkTime = 400, split = 2000, showMapError = False, showTrajectories = False, showHist = False))
        except:
            print("eigenvalue error occured.")

    return -1*np.mean(results)

def trainAndTest(alph):

    results = np.array([])
    num_res = 10

    for i in range(num_res):
        try:
            ic = np.random.rand(3)*2-1
            rk = RungeKutta(x0 = ic[0], y0 = ic[1], z0 = 30*ic[2], T = 500, ttsplit = int(500/0.1), noise_scaling = 0.01)
            res = Reservoir(rk, rsvr_size = 100, spectral_radius = 0.5, input_weight = 1.0)
            
            trainRRM(res, rk, skip = 150, alpha = alph)
            
            results = np.append(results, test(res, 1, rkTime = 400, split = 2000, showMapError = False, showTrajectories = False, showHist = False))
        except:
            print("eigenvalue error occured.")
    return -1*np.mean(results)



########################################
np.random.seed(0)

train_time = 200
res_size = 100
res_per_test = 50
noise_values = np.logspace(-3.666666666666, 0, num = 12, base = 10)
alpha_values = np.logspace(-8, -2, 13)
stable_frac  = np.zeros(noise_values.size)
stable_frac_alpha  = np.zeros(noise_values.size)


#rk = RungeKutta(x0 = 1, y0 = 1, z0 = 30, T = train_time, ttsplit = int(train_time/0.1), noise_scaling = 0.01)
#reservoirs = generate_res(res_per_test, rk, res_size = res_size)

for i, noise in enumerate(noise_values):
    ic = np.random.rand(3)*2-1
    rk = RungeKutta(x0 = ic[0], y0 = ic[1], z0 = 30*ic[2], T = train_time, ttsplit = int(train_time/0.1), noise_scaling = noise)
    
    reservoirs = generate_res(res_per_test, rk, res_size = res_size)
    #for r in reservoirs:
        #r.data_trstates = 0
        #r.states_trstates = 0 
    #    get_states(r, rk, skip = 150)

    min_optim_func = lambda alpha: optim_func(reservoirs, alpha)
    func_vals = np.zeros(alpha_values.size)
    for j in range(alpha_values.size):
        func_vals[j] = min_optim_func(alpha_values[j])
    result_fun = np.min(func_vals)
    result_x   = alpha_values[np.argmin(func_vals)]
    stable_frac[i] = -result_fun    
    stable_frac_alpha[i] = result_x
    """
    f = open("noise varying data", "a")
    now = datetime.now()
    currenttime = now.strftime("%H:%M:%S")
    f.write(currenttime)
    f.write("\n")
    f.write("noise level: " + str(noise))
    f.write("\n")
    f.write("res size: " + str(res_size))
    f.write("\n")
    f.write("train time: " + str(train_time))
    f.write("\n")
    f.write("max fraction of stable reservoirs: " + str(-1*result_fun))
    f.write("\n")
    f.write("optimal alpha: " + str(result_x))
    f.write("\n")
    f.write("\n")
    f.close()
    """

np.savetxt('stable_frac_%dnodes_%dtrainiters.csv' %(res_size, train_time), stable_frac, delimiter = ',')
np.savetxt('stable_frac_alpha_%dnodes_%dtrainiters.csv' %(res_size, train_time), stable_frac_alpha, delimiter = ',')

Test 0 valid time: 44
Variance of lorenz data x dim: 1.0025923518812798
Variance of predictions: 0.9746143106671178
Max of total square error: 0.023344698856819907
Mean of total error: 0.0006182326649912118
Wasserstein distance: 0.14291288959359033

unstable

Avg. max sum square: 0.023344698856819907
Avg. mean sum square: 0.0006182326649912118
Avg. of x dim: -0.1877736451989875
Var. of x dim: 0.9746143106671178

Test 0 valid time: 60
Variance of lorenz data x dim: 0.9864679535954116
Variance of predictions: 0.14296698440031724
Max of total square error: 17.4889596124652
Mean of total error: 3.849394800159621
Wasserstein distance: 1.3007009296166137

unstable

Avg. max sum square: 17.4889596124652
Avg. mean sum square: 3.849394800159621
Avg. of x dim: -1.4118413817822044
Var. of x dim: 0.14296698440031724

Test 0 valid time: 49
Variance of lorenz data x dim: 0.9834422493096303
Variance of predictions: 0.9980359305043958
Max of total square error: 0.020097260193482635
Mean of total error

c:\users\alexander\anaconda3\envs\reservoir-rls\lib\site-packages\ipykernel_launcher.py:213: RuntimeWarning: overflow encountered in matmul
c:\users\alexander\anaconda3\envs\reservoir-rls\lib\site-packages\ipykernel_launcher.py:213: RuntimeWarning: invalid value encountered in matmul
c:\users\alexander\anaconda3\envs\reservoir-rls\lib\site-packages\ipykernel_launcher.py:250: RuntimeWarning: overflow encountered in double_scalars



Variance of predictions: nan
Max of total square error: 49106.09586062606
Mean of total error: nan
Wasserstein distance: nan

unstable

Avg. max sum square: 49106.09586062606
Avg. mean sum square: nan
Avg. of x dim: nan
Var. of x dim: nan

Test 0 valid time: 30
Variance of lorenz data x dim: 0.9884455226650148
Variance of predictions: nan
Max of total square error: 1107112.210268976
Mean of total error: nan
Wasserstein distance: nan

unstable

Avg. max sum square: 1107112.210268976
Avg. mean sum square: nan
Avg. of x dim: nan
Var. of x dim: nan

Test 0 valid time: 37
Variance of lorenz data x dim: 0.9916490272560292
Variance of predictions: nan
Max of total square error: 23628.209963825615
Mean of total error: nan
Wasserstein distance: nan

unstable

Avg. max sum square: 23628.209963825615
Avg. mean sum square: nan
Avg. of x dim: nan
Var. of x dim: nan

Test 0 valid time: 57
Variance of lorenz data x dim: 0.9940733434300448
Variance of predictions: 0.9447587985518355
Max of total squa

Wasserstein distance: 0.4499398524756072

unstable

Avg. max sum square: 90.04987504229734
Avg. mean sum square: 10.689520696674288
Avg. of x dim: -0.08813579489161884
Var. of x dim: 2.437712070126961

Test 0 valid time: 34
Variance of lorenz data x dim: 0.9888609435905579
Variance of predictions: 1.0360828709475802
Max of total square error: 16.850977311566115
Mean of total error: 0.7008206322929854
Wasserstein distance: 0.132882996130826

unstable

Avg. max sum square: 16.850977311566115
Avg. mean sum square: 0.7008206322929854
Avg. of x dim: -0.22478867735396166
Var. of x dim: 1.0360828709475802

Test 0 valid time: 47
Variance of lorenz data x dim: 0.999671084431316
Variance of predictions: 1.006904316972896
Max of total square error: 0.04556741260696359
Mean of total error: 0.0006878181609962328
Wasserstein distance: 0.0714920833679864

stable

Avg. max sum square: 0.04556741260696359
Avg. mean sum square: 0.0006878181609962328
Avg. of x dim: -0.00013891653681122722
Var. of x dim: 

c:\users\alexander\anaconda3\envs\reservoir-rls\lib\site-packages\ipykernel_launcher.py:254: RuntimeWarning: overflow encountered in double_scalars
c:\users\alexander\anaconda3\envs\reservoir-rls\lib\site-packages\numpy\core\_methods.py:205: RuntimeWarning: overflow encountered in multiply
  x = um.multiply(x, x, out=x)


...

Variance of lorenz data x dim: 1.0002583511364005
Variance of predictions: 0.0731151822743494
Max of total square error: 0.3585861785492197
Mean of total error: 0.11053311049147976
Wasserstein distance: 0.992622974515678

unstable

Avg. max sum square: 0.3585861785492197
Avg. mean sum square: 0.11053311049147976
Avg. of x dim: 0.9229152229354456
Var. of x dim: 0.0731151822743494

Test 0 valid time: 10
Variance of lorenz data x dim: 0.9961065835212012
Variance of predictions: 0.0009371815869033654
Max of total square error: 0.1496109162880816
Mean of total error: 0.03232207908002884
Wasserstein distance: 1.2072498815566166

unstable

Avg. max sum square: 0.1496109162880816
Avg. mean sum square: 0.03232207908002884
Avg. of x dim: -0.9704709464515983
Var. of x dim: 0.0009371815869033654

Test 0 valid time: 22
Variance of lorenz data x dim: 0.9965573811613972
Variance of predictions: 0.21451701085607253
Max of total square error: 0.239988222466487
Mean of total error: 0.09396853917057336
W

Variance of lorenz data x dim: 0.9903715424558238
Variance of predictions: 0.16595893149150695
Max of total square error: 0.8861880527115172
Mean of total error: 0.08550958871566583
Wasserstein distance: 0.9809746019955319

unstable

Avg. max sum square: 0.8861880527115172
Avg. mean sum square: 0.08550958871566583
Avg. of x dim: -1.0346208544665643
Var. of x dim: 0.16595893149150695

Test 0 valid time: 8
Variance of lorenz data x dim: 0.9895000008104985
Variance of predictions: 0.0011016447868170038
Max of total square error: 0.43236186481338845
Mean of total error: 0.007110058987026217
Wasserstein distance: 1.1545346556188751

unstable

Avg. max sum square: 0.43236186481338845
Avg. mean sum square: 0.007110058987026217
Avg. of x dim: -1.0914436088376758
Var. of x dim: 0.0011016447868170038

Test 0 valid time: 13
Variance of lorenz data x dim: 0.9949966653347029
Variance of predictions: 0.0390058679333296
Max of total square error: 0.10738597437520359
Mean of total error: 0.02483272579

Variance of lorenz data x dim: 0.9898161618186242
Variance of predictions: 0.16529280247037792
Max of total square error: 0.16050995279169278
Mean of total error: 0.04207021133299669
Wasserstein distance: 1.0214396342396541

unstable

Avg. max sum square: 0.16050995279169278
Avg. mean sum square: 0.04207021133299669
Avg. of x dim: -1.0926060127433193
Var. of x dim: 0.16529280247037792

Test 0 valid time: 20
Variance of lorenz data x dim: 0.9905850827362471
Variance of predictions: 0.0020409478391846623
Max of total square error: 0.19578857763590188
Mean of total error: 0.06469846960210984
Wasserstein distance: 1.1159351162665874

unstable

Avg. max sum square: 0.19578857763590188
Avg. mean sum square: 0.06469846960210984
Avg. of x dim: -1.0145701914489176
Var. of x dim: 0.0020409478391846623

Test 0 valid time: 8
Variance of lorenz data x dim: 0.9938455186991294
Variance of predictions: 0.013307425692820346
Max of total square error: 0.5809579314417029
Mean of total error: 0.0289381992

Variance of lorenz data x dim: 0.9855969563353394
Variance of predictions: 0.015022985370661542
Max of total square error: 0.6736755979680421
Mean of total error: 0.01675763767068578
Wasserstein distance: 1.1364648897832226

unstable

Avg. max sum square: 0.6736755979680421
Avg. mean sum square: 0.01675763767068578
Avg. of x dim: -1.1242299940179485
Var. of x dim: 0.015022985370661542

Test 0 valid time: 6
Variance of lorenz data x dim: 1.0001793502703418
Variance of predictions: 0.03726779664147079
Max of total square error: 0.6531877676877333
Mean of total error: 0.15203932480881946
Wasserstein distance: 0.9817146501322318

unstable

Avg. max sum square: 0.6531877676877333
Avg. mean sum square: 0.15203932480881946
Avg. of x dim: 0.8544777481806425
Var. of x dim: 0.03726779664147079

Test 0 valid time: 5
Variance of lorenz data x dim: 0.9917680738614832
Variance of predictions: 0.1018474402765542
Max of total square error: 0.686378132599488
Mean of total error: 0.059074557524850246
Wa

Wasserstein distance: 1.1779475121815344

unstable

Avg. max sum square: 0.1701212880547723
Avg. mean sum square: 0.0611904034238639
Avg. of x dim: -1.0934492711382116
Var. of x dim: 0.09773337975500392

Test 0 valid time: 25
Variance of lorenz data x dim: 0.9972065814272252
Variance of predictions: 0.041509190997599775
Max of total square error: 0.7460256631208051
Mean of total error: 0.17033882133617212
Wasserstein distance: 0.9770705310040327

unstable

Avg. max sum square: 0.7460256631208051
Avg. mean sum square: 0.17033882133617212
Avg. of x dim: 0.815762380079032
Var. of x dim: 0.041509190997599775

Test 0 valid time: 7
Variance of lorenz data x dim: 0.9883731422256241
Variance of predictions: 0.0009125149220133998
Max of total square error: 0.6331095799084792
Mean of total error: 0.003666865937658742
Wasserstein distance: 1.3534655042961106

unstable

Avg. max sum square: 0.6331095799084792
Avg. mean sum square: 0.003666865937658742
Avg. of x dim: -1.1317935737011222
Var. of x d